In [9]:
import json
import random
import numpy as np
import pandas as pd
from tqdm import tqdm
from openai import OpenAI, AzureOpenAI

In [10]:
client = AzureOpenAI(
            azure_endpoint="https://cullmsouthindia.openai.azure.com/",
            api_key="037155e1b16a432fa836637370eca0e3",
            api_version="2024-02-15-preview",
        )

In [11]:
dataset = json.load(open("cleaned_final_modeLing.json",'r'))
dataset[0]

{'name': 'Abun',
 'type': ['POSS'],
 'difficulty': 5,
 'data': ["Abun: gap sye bi gan\nEnglish: big rat's offspring",
  'Abun: ji bi ngwe\nEnglish: my garden',
  'Abun: ji syim\nEnglish: my arm',
  "Abun: ndar sye gwes\nEnglish: big dog's leg",
  "Abun: gap bi ngwe\nEnglish: rat's garden"],
 'questions': ['Abun: ji gwes',
  'Abun: ji bi gan',
  'English: my big garden',
  "English: dog's offspring"],
 'answers': ['English: my leg',
  'English: my offspring',
  'Abun: ji bi ngwe sye',
  'Abun: ndar bi gan'],
 'cleaned_data': {'data': [[['Abun', 'gap sye bi gan'],
    ['English', "big rat's offspring"]],
   [['Abun', 'ji bi ngwe'], ['English', 'my garden']],
   [['Abun', 'ji syim'], ['English', 'my arm']],
   [['Abun', 'ndar sye gwes'], ['English', "big dog's leg"]],
   [['Abun', 'gap bi ngwe'], ['English', "rat's garden"]]],
  'qna': [[['Abun', 'ji gwes'], ['English', 'my leg']],
   [['Abun', 'ji bi gan'], ['English', 'my offspring']],
   [['English', 'my big garden'], ['Abun', 'ji bi n

In [12]:
dataset

[{'name': 'Abun',
  'type': ['POSS'],
  'difficulty': 5,
  'data': ["Abun: gap sye bi gan\nEnglish: big rat's offspring",
   'Abun: ji bi ngwe\nEnglish: my garden',
   'Abun: ji syim\nEnglish: my arm',
   "Abun: ndar sye gwes\nEnglish: big dog's leg",
   "Abun: gap bi ngwe\nEnglish: rat's garden"],
  'questions': ['Abun: ji gwes',
   'Abun: ji bi gan',
   'English: my big garden',
   "English: dog's offspring"],
  'answers': ['English: my leg',
   'English: my offspring',
   'Abun: ji bi ngwe sye',
   'Abun: ndar bi gan'],
  'cleaned_data': {'data': [[['Abun', 'gap sye bi gan'],
     ['English', "big rat's offspring"]],
    [['Abun', 'ji bi ngwe'], ['English', 'my garden']],
    [['Abun', 'ji syim'], ['English', 'my arm']],
    [['Abun', 'ndar sye gwes'], ['English', "big dog's leg"]],
    [['Abun', 'gap bi ngwe'], ['English', "rat's garden"]]],
   'qna': [[['Abun', 'ji gwes'], ['English', 'my leg']],
    [['Abun', 'ji bi gan'], ['English', 'my offspring']],
    [['English', 'my big ga

In [13]:
def legacy_question_data_to_puzzle_prompt(core_question_data):
    BASE_PROMPT = """This is a linguistics puzzle. Below are some expressions in an unknown language and their English translations. 

The puzzle is completely solvable. All of your answers should rely only on reasoning from the given data. Do not use any external knowledge. 

<DATA>

Here are the following questions. Please translate them.

<QUESTIONS>

"""

    data_pairs = []
    for pair in core_question_data["data"]:
        data_pairs.append(f"\t\"{pair[0][0]}\":\"{pair[0][1]}\"\n\t\"{pair[1][0]}\":\"{pair[1][1]}\"")
    
    question_pairs = []
    for pair in core_question_data["qna"]:
        question_pairs.append(f"\t\"{pair[0][0]}\":\"{pair[0][1]}\"")

    return BASE_PROMPT.replace("<DATA>",',\n\n'.join(data_pairs)).replace("<QUESTIONS>",',\n'.join(question_pairs))


In [14]:
legacy_question_data_to_puzzle_prompt(dataset[0]["cleaned_data"])

'This is a linguistics puzzle. Below are some expressions in an unknown language and their English translations. \n\nThe puzzle is completely solvable. All of your answers should rely only on reasoning from the given data. Do not use any external knowledge. \n\n\t"Abun":"gap sye bi gan"\n\t"English":"big rat\'s offspring",\n\n\t"Abun":"ji bi ngwe"\n\t"English":"my garden",\n\n\t"Abun":"ji syim"\n\t"English":"my arm",\n\n\t"Abun":"ndar sye gwes"\n\t"English":"big dog\'s leg",\n\n\t"Abun":"gap bi ngwe"\n\t"English":"rat\'s garden"\n\nHere are the following questions. Please translate them.\n\n\t"Abun":"ji gwes",\n\t"Abun":"ji bi gan",\n\t"English":"my big garden",\n\t"English":"dog\'s offspring"\n\n'

In [15]:
def question_data_to_puzzle_prompt(core_question_data, exemplar_question_data):
    BASE_PROMPT = """This is a linguistics puzzle. Below are some expressions in an unknown language and their English translations. 

The puzzle is completely solvable. All of your answers should rely only on reasoning from the given data. Do not use any external knowledge. 

<CORE_DATA>

Here are the following questions. Please translate them.

<CORE_QUESTIONS>

To help you out, here is an example of another similar problem, _with solutions_. Try and understand how this problem was solved, and use that understanding to solve the new problem. 

"Problem statement: This is a linguistics puzzle. Below are some expressions in an unknown language and their English translations. 

The puzzle is completely solvable. All of your answers should rely only on reasoning from the given data. Do not use any external knowledge. 

<EXEMPLAR_DATA>

Here are the following questions. Please translate them.

<EXEMPLAR_QUESTIONS>

ANSWERS:

<EXEMPLAR_ANSWERS>

"""

    core_data_pairs = []
    for pair in core_question_data["data"]:
        core_data_pairs.append(f"\t\"{pair[0][0]}\": \"{pair[0][1]}\"\n\t\"{pair[1][0]}\":\"{pair[1][1]}\"")
    
    core_question_pairs = []
    for pair in core_question_data["qna"]:
        core_question_pairs.append(f"\t\"{pair[0][0]}\": \"{pair[0][1]}\"")

    exemplar_data_pairs = []
    for pair in exemplar_question_data["data"]:
        exemplar_data_pairs.append(f"\t\"{pair[0][0]}\": \"{pair[0][1]}\"\n\t\"{pair[1][0]}\":\"{pair[1][1]}\"")

    exemplar_question_pairs = []
    for pair in exemplar_question_data["qna"]:
        exemplar_question_pairs.append(f"\t\"{pair[0][0]}\": \"{pair[0][1]}\"")

    exemplar_answer_pairs = []
    for pair in exemplar_question_data["qna"]:
        exemplar_answer_pairs.append(f"\t\"{pair[1][0]}\": \"{pair[1][1]}\"")

    return BASE_PROMPT.replace(
        "<CORE_DATA>",',\n\n'.join(core_data_pairs)
    ).replace(
        "<CORE_QUESTIONS>",',\n'.join(core_question_pairs)
    ).replace(
        "<EXEMPLAR_DATA>",',\n\n'.join(exemplar_data_pairs)
    ).replace(
        "<EXEMPLAR_QUESTIONS>",',\n'.join(exemplar_question_pairs)
    ).replace(
        "<EXEMPLAR_ANSWERS>",',\n'.join(exemplar_answer_pairs)
    )

print(question_data_to_puzzle_prompt(dataset[0]["cleaned_data"], dataset[1]["cleaned_data"]))

This is a linguistics puzzle. Below are some expressions in an unknown language and their English translations. 

The puzzle is completely solvable. All of your answers should rely only on reasoning from the given data. Do not use any external knowledge. 

	"Abun": "gap sye bi gan"
	"English":"big rat's offspring",

	"Abun": "ji bi ngwe"
	"English":"my garden",

	"Abun": "ji syim"
	"English":"my arm",

	"Abun": "ndar sye gwes"
	"English":"big dog's leg",

	"Abun": "gap bi ngwe"
	"English":"rat's garden"

Here are the following questions. Please translate them.

	"Abun": "ji gwes",
	"Abun": "ji bi gan",
	"English": "my big garden",
	"English": "dog's offspring"

To help you out, here is an example of another similar problem, _with solutions_. Try and understand how this problem was solved, and use that understanding to solve the new problem. 

"Problem statement: This is a linguistics puzzle. Below are some expressions in an unknown language and their English translations. 

The puzzle 

In [16]:
def fetch_solution_text(core_question_data, exemplar_question_data):

    prompt = question_data_to_puzzle_prompt(core_question_data, exemplar_question_data)
    message = [
    {"role": "system", "content": "You are a helpful assistant."},
    # {"role": "system", "content": "You are a helpful assistant. Response only using valid JSON objects."},
    {
        "role": "user",
        "content": prompt,
    },
    ]

    # print(message)

    max_retry = 3
    while max_retry > 0:
        try:
            response = client.chat.completions.create(
                model="gpt4",
                messages=message,
                temperature=0,
                max_tokens=2048,
                # response_format={"type": "json_object"},
                seed=7777
            )

            result = response.choices[0].message.content.strip()
            return result
        except:
            print("error in JSONDecodeError")
            max_retry -= 1
    return ""

# fetch_solution_text(dataset[0]["cleaned_data"])

In [17]:
def fetch_final_answer_JSON(core_question_data, auto_solution, verbose_error=False):

    # Set as "INVALID" if no valid answer is detected.
    pairs = []
    for pair in core_question_data["qna"]:

        pairs.append("""
        {
            "<LANG0>": "<ANS0>",
            "<LANG1>": "" # Corresponding answer from solution.
        }
""".replace("<LANG0>",pair[0][0]).replace("<LANG1>",pair[1][0]).replace("<ANS0>",pair[0][1]))
        
        json_format = "{\n\t\"answers\": [\n" + ',\n'.join(pairs) + "\t]\n}"

    core_problem_prompt = legacy_question_data_to_puzzle_prompt(core_question_data)

    message_text = [
    # {"role": "system", "content": "You are a helpful assistant."},
    {"role": "system", "content": "You are a helpful assistant. Respond only using valid JSON objects."},
    {
        "role": "user",
        "content": """Observe the following linguistics puzzle.

--- puzzle start ---
<CORE_PROBLEM>
--- puzzle end ---

Here's a possible solution to the puzzle. 

--- solution start ---
<AUTO_SOLUTION>
--- solution end ---

Extract the final answers for the questions listed in the puzzle from the solution as a valid JSON in the following format:

--- JSON format start ---
<JSON_FORMAT>
--- JSON format end ---

Do not try to solve the puzzle yourself or modify the answers from the given solution in any way.
""".replace("<CORE_PROBLEM>",core_problem_prompt).replace("<AUTO_SOLUTION>",auto_solution).replace("<JSON_FORMAT>",json_format),
    },
    ]

    # print(message_text[1]["content"])

    max_retry = 3
    while max_retry > 0:
        try:
            response = client.chat.completions.create(
                model="gpt4",
                messages=message_text,
                temperature=0,
                max_tokens=2048,
                response_format={"type": "json_object"},
                seed=7777
            )
            try:
                result = json.loads(response.choices[0].message.content)
            except: 
                if verbose_error: 
                    print({
                        "solution": auto_solution,
                        "response": response.choices[0].message.content
                    })
                raise Execption("JSON decoding failed")
            return result
        except:
            print("error in JSONDecodeError")
            max_retry -= 1
    return ""

In [18]:
for qid, d in enumerate(dataset):
    d["qid"] = qid

In [19]:
q_type_pools = {}

for d in dataset:
    typ = d["type"][0]
    if typ not in q_type_pools:
        q_type_pools[typ] = list(range(len(dataset)))
    # q_type_pools[typ].append(d["qid"])

print(q_type_pools)

{'POSS': [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47], 'ORDER': [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47], 'NOUN-ADJ': [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47], 'SEM': [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47]}


In [20]:
pair_dataset = {}

for d in dataset:
    for e in dataset:
        if d["qid"]==e["qid"]:
            continue
        # if d["type"][0]!=e["type"][0]:
        #     continue
        pair_dataset[(d["qid"],e["qid"])] = {
            "core": d.copy(),
            "exemplar": e.copy(),
            "response": None
        }
len(pair_dataset)

2256

In [21]:
pair_dataset

{(0,
  1): {'core': {'name': 'Abun',
   'type': ['POSS'],
   'difficulty': 5,
   'data': ["Abun: gap sye bi gan\nEnglish: big rat's offspring",
    'Abun: ji bi ngwe\nEnglish: my garden',
    'Abun: ji syim\nEnglish: my arm',
    "Abun: ndar sye gwes\nEnglish: big dog's leg",
    "Abun: gap bi ngwe\nEnglish: rat's garden"],
   'questions': ['Abun: ji gwes',
    'Abun: ji bi gan',
    'English: my big garden',
    "English: dog's offspring"],
   'answers': ['English: my leg',
    'English: my offspring',
    'Abun: ji bi ngwe sye',
    'Abun: ndar bi gan'],
   'cleaned_data': {'data': [[['Abun', 'gap sye bi gan'],
      ['English', "big rat's offspring"]],
     [['Abun', 'ji bi ngwe'], ['English', 'my garden']],
     [['Abun', 'ji syim'], ['English', 'my arm']],
     [['Abun', 'ndar sye gwes'], ['English', "big dog's leg"]],
     [['Abun', 'gap bi ngwe'], ['English', "rat's garden"]]],
    'qna': [[['Abun', 'ji gwes'], ['English', 'my leg']],
     [['Abun', 'ji bi gan'], ['English', 'my

In [22]:
# remaining count
total, count = 0, 0
for (didx, eidx), pdata in pair_dataset.items():
    d, e = pdata["core"], pdata["exemplar"]
    if pair_dataset[(didx, eidx)]["response"] == None:
        count += 1
    total += 1
print(count, total)

2256 2256


In [23]:
pbar = tqdm(total=len(pair_dataset))

for (didx, eidx), pdata in pair_dataset.items():
    d, e = pdata["core"], pdata["exemplar"]
    if pair_dataset[(didx, eidx)]["response"] != None:
        continue
    try:
        s = fetch_solution_text(d["cleaned_data"], e["cleaned_data"])
        if s == "":
            raise Exception()
        j = fetch_final_answer_JSON(d["cleaned_data"], s)
        pair_dataset[(didx, eidx)]["response"] = {
            "solution": s,
            "answer": j,
        }
        # print(didx, eidx)
        # break
    except:
        json.dump(pair_dataset, open("v8_responses_safekeep.json",'w'))
        raise Exception()
        
    pbar.update(1)

  0%|          | 7/2256 [02:48<14:31:44, 23.26s/it]

error in JSONDecodeError
error in JSONDecodeError


In [ ]:
import pickle
pickle.dump(pair_dataset, open("v8_responses_safekeep.pkl",'wb'))

In [ ]:
pair_dataset[(0,1)]['response']['answer']['answers']

{'answers': [{'Abun': 'ji gwes', 'English': 'my leg'},
  {'Abun': 'ji bi gan', 'English': 'my offspring'},
  {'English': 'my big garden', 'Abun': 'ji sye bi ngwe'},
  {'English': "dog's offspring", 'Abun': 'ndar bi gan'}]}

In [ ]:
pair_dataset[(0,1)]['core']['cleaned_data']['qna']

[[['Abun', 'ji gwes'], ['English', 'my leg']],
 [['Abun', 'ji bi gan'], ['English', 'my offspring']],
 [['English', 'my big garden'], ['Abun', 'ji bi ngwe sye']],
 [['English', "dog's offspring"], ['Abun', 'ndar bi gan']]]

In [ ]:
def get_batch_exact_math_score(pair):
    correct, total = 0, 0
    for g, a in zip(pair['core']['cleaned_data']['qna'], pair['response']['answer']['answers']):
        g_lang, g_s = g[1]
        a_s = str(a[g_lang])
        total += 1
        if a_s!="None" and g_s.strip() == a_s.strip():
            correct += 1
    return (correct, total)

get_batch_exact_math_score(pair_dataset[(0,1)])

(3, 4)

In [ ]:
pair_scores = {}
for key, pair in pair_dataset.items():
    try: 
        pair_scores[key] = get_batch_exact_math_score(pair)
    except:
        display(pair)
        raise Exception()
pair_scores

{(0, 1): (3, 4),
 (0, 2): (1, 4),
 (0, 3): (1, 4),
 (0, 4): (3, 4),
 (0, 5): (2, 4),
 (0, 6): (3, 4),
 (0, 7): (1, 4),
 (0, 8): (3, 4),
 (0, 9): (3, 4),
 (0, 10): (2, 4),
 (0, 11): (3, 4),
 (0, 12): (1, 4),
 (0, 13): (3, 4),
 (0, 14): (3, 4),
 (0, 15): (3, 4),
 (0, 16): (3, 4),
 (0, 17): (3, 4),
 (0, 18): (3, 4),
 (0, 19): (3, 4),
 (0, 20): (3, 4),
 (0, 21): (3, 4),
 (0, 22): (3, 4),
 (0, 23): (3, 4),
 (0, 24): (1, 4),
 (0, 25): (3, 4),
 (0, 26): (3, 4),
 (0, 27): (3, 4),
 (0, 28): (3, 4),
 (0, 29): (3, 4),
 (0, 30): (3, 4),
 (0, 31): (1, 4),
 (0, 32): (3, 4),
 (0, 33): (3, 4),
 (0, 34): (2, 4),
 (0, 35): (3, 4),
 (0, 36): (3, 4),
 (0, 37): (3, 4),
 (0, 38): (3, 4),
 (0, 39): (3, 4),
 (0, 40): (3, 4),
 (0, 41): (2, 4),
 (0, 42): (3, 4),
 (0, 43): (3, 4),
 (0, 44): (3, 4),
 (0, 45): (1, 4),
 (0, 46): (2, 4),
 (0, 47): (2, 4),
 (1, 0): (0, 8),
 (1, 2): (0, 8),
 (1, 3): (0, 8),
 (1, 4): (0, 8),
 (1, 5): (1, 8),
 (1, 6): (1, 8),
 (1, 7): (0, 8),
 (1, 8): (0, 8),
 (1, 9): (0, 8),
 (1, 10): 

In [ ]:
idx_max = max([_p for pidx in pair_scores.keys() for _p in pidx])
print(idx_max)

pair_score_mat = np.zeros((idx_max+1,idx_max+1))
pair_count_mat = np.zeros((idx_max+1,idx_max+1))
for i in range(idx_max + 1):
    for j in range(idx_max + 1):
        if i==j:
            continue
        pair_score_mat[i][j], pair_count_mat[i][j] = pair_scores[(i,j)]

47


In [ ]:
masked_pair_score_mat = np.ma.masked_array(pair_score_mat, np.eye(pair_score_mat.shape[0]))
masked_pair_count_mat = np.ma.masked_array(pair_count_mat, np.eye(pair_count_mat.shape[0]))

In [ ]:
print(sum(np.max(masked_pair_score_mat, axis=1)) / sum(np.max(masked_pair_count_mat, axis=1)))
print(sum(np.mean(masked_pair_score_mat, axis=1)) / sum(np.max(masked_pair_count_mat, axis=1)))
print(sum(np.min(masked_pair_score_mat, axis=1)) / sum(np.max(masked_pair_count_mat, axis=1)))

0.7022058823529411
0.5639080100125158
0.3713235294117647


In [ ]:
masked_pair_accuracy_mat = masked_pair_score_mat / masked_pair_count_mat
masked_pair_accuracy_mat

masked_array(
  data=[[--, 0.75, 0.25, ..., 0.25, 0.5, 0.5],
        [0.0, --, 0.0, ..., 0.0, 0.125, 0.0],
        [0.25, 0.25, --, ..., 0.0, 0.25, 0.25],
        ...,
        [0.2, 0.2, 0.4, ..., --, 0.4, 0.4],
        [0.75, 0.5, 0.5, ..., 0.625, --, 0.625],
        [0.0, 0.0, 0.16666666666666666, ..., 0.16666666666666666, 0.0,
         --]],
  mask=[[ True, False, False, ..., False, False, False],
        [False,  True, False, ..., False, False, False],
        [False, False,  True, ..., False, False, False],
        ...,
        [False, False, False, ...,  True, False, False],
        [False, False, False, ..., False,  True, False],
        [False, False, False, ..., False, False,  True]],
  fill_value=1e+20)

In [ ]:
pair_dataframe = []
for (didx, eidx), pdata in pair_dataset.items():
    d, e = pdata["core"], pdata["exemplar"]
    pair_dataframe.append({
        "core_qid": didx, "exmp_qid": eidx,
        "core_name": d["name"], "exmp_name": e["name"],
        "core_type": d["type"][0], "exmp_type": e["type"][0],
        "core_difficulty": d["difficulty"], "exmp_difficulty": e["difficulty"],
        "correct": masked_pair_score_mat[didx][eidx],
        "total": masked_pair_count_mat[didx][eidx],
        "accuracy": masked_pair_accuracy_mat[didx][eidx],
    })
pair_dataframe = pd.DataFrame(pair_dataframe)
pair_dataframe

core_qid  exmp_qid core_name    exmp_name core_type exmp_type  \
0            0         1      Abun         Ainu      POSS     ORDER   
1            0         2      Abun  Ayutla Mixe      POSS     ORDER   
2            0         3      Abun      Bangime      POSS     ORDER   
3            0         4      Abun    Bangime 2      POSS     ORDER   
4            0         5      Abun    Bangime 3      POSS     ORDER   
...        ...       ...       ...          ...       ...       ...   
2251        47        42   Totonac   Rapa Nui 7      POSS  NOUN-ADJ   
2252        47        43   Totonac         Seri      POSS  NOUN-ADJ   
2253        47        44   Totonac       Seri 2      POSS     ORDER   
2254        47        45   Totonac       Seri 3      POSS       SEM   
2255        47        46   Totonac       Seri 4      POSS      POSS   

      core_difficulty  exmp_difficulty  correct  total  accuracy  
0                   5                5      3.0    4.0  0.750000  
1                   5                4      1.0    4.0  0.250000  
2                   5                3      1.0    4.0  0.250000  
3                   5                1      3.0    4.0  0.750000  
4                   5                4      2.0    4.0  0.500000  
...               ...              ...      ...    ...       ...  
2251                5                3      1.0    6.0  0.166667  
2252                5                5      0.0    6.0  0.000000  
2253                5                5      1.0    6.0  0.166667  
2254                5                5      1.0    6.0  0.166667  
2255                5                5      0.0    6.0  0.000000  

[2256 rows x 11 columns]

In [ ]:
pair_dataframe.to_csv("pair_dataframe.csv", index=False)

In [ ]:
pickle.dump(pair_dataset, open("pair_dataset.pkl",'wb'))

In [ ]:
pickle.dump({
    "masked_pair_score_mat": masked_pair_score_mat,
    "masked_pair_count_mat": masked_pair_count_mat,
}, open("masked_pair_mats.pkl",'wb'))

In [ ]:
baseline_df = pd.read_csv("ModeLing_baseline_eval_v3.csv")
baseline_df["score"] = baseline_df["target_sentence_gold"] == baseline_df["target_sentence_auto"]
baseline_df

problem_name   type  difficulty  \
0           Abun   POSS           5   
1           Abun   POSS           5   
2           Abun   POSS           5   
3           Abun   POSS           5   
4           Ainu  ORDER           5   
..           ...    ...         ...   
267      Totonac   POSS           5   
268      Totonac   POSS           5   
269      Totonac   POSS           5   
270      Totonac   POSS           5   
271      Totonac   POSS           5   

                                                  data  \
0    [[["Abun", "gap sye bi gan"], ["English", "big...   
1    [[["Abun", "gap sye bi gan"], ["English", "big...   
2    [[["Abun", "gap sye bi gan"], ["English", "big...   
3    [[["Abun", "gap sye bi gan"], ["English", "big...   
4    [[["Ainu", "Numan hambaga ku=e."], ["English",...   
..                                                 ...   
267  [[["Totonac", "\u0161at\u00e9ko"], ["English",...   
268  [[["Totonac", "\u0161at\u00e9ko"], ["English",...   
269  [[["Totonac", "\u0161at\u00e9ko"], ["English",...   
270  [[["Totonac", "\u0161at\u00e9ko"], ["English",...   
271  [[["Totonac", "\u0161at\u00e9ko"], ["English",...   

                                         solution_auto source_lang  \
0    Based on the provided examples, we can try to ...        Abun   
1    Based on the provided examples, we can try to ...        Abun   
2    Based on the provided examples, we can try to ...     English   
3    Based on the provided examples, we can try to ...     English   
4    Based on the provided Ainu to English translat...        Ainu   
..                                                 ...         ...   
267  Based on the provided examples, we can attempt...     Totonac   
268  Based on the provided examples, we can attempt...     Totonac   
269  Based on the provided examples, we can attempt...     English   
270  Based on the provided examples, we can attempt...     English   
271  Based on the provided examples, we can attempt...     English   

                source_sentence target_lang       target_sentence_gold  \
0                       ji gwes     English                     my leg   
1                     ji bi gan     English               my offspring   
2                 my big garden        Abun             ji bi ngwe sye   
3               dog's offspring        Abun                ndar bi gan   
4    Tan kimunkamuy poro cep e.     English  This bear ate a big fish.   
..                          ...         ...                        ...   
267                       šakám     English                      child   
268                 kinčičiikám     English                   our dogs   
269                        vein     Totonac                    šnúxuti   
270                  their dogs     Totonac                  ščičiikám   
271              their children     Totonac                    škamkám   

                target_sentence_auto  score  
0                             my leg   True  
1                       my offspring   True  
2                        ji sye ngwe  False  
3                        ndar bi gan   True  
4    The bear is very big and jumps.  False  
..                               ...    ...  
267                       their dogs  False  
268                   their children  False  
269                             kúsi  False  
270                            šakám  False  
271                      kinčičiikám  False  

[272 rows x 11 columns]

In [ ]:
unit_dataframe = []
for idx in range(pair_score_mat.shape[0]):
    d = dataset[idx]
    unit_dataframe.append({
        "qid": idx,
        "name": d["name"],
        "type": d["type"][0],
        "difficulty": d["difficulty"],

        "max_accuracy_as_core": np.max(masked_pair_accuracy_mat[idx,:]),
        "mean_accuracy_as_core": np.mean(masked_pair_accuracy_mat[idx,:]),
        "min_accuracy_as_core": np.min(masked_pair_accuracy_mat[idx,:]),

        "mean_accuracy_as_exemplar": np.mean(masked_pair_accuracy_mat[:,idx]),

        "data": d["data"],
        "questions": d["questions"],
        "answers": d["answers"],
    })
unit_dataframe = pd.DataFrame(unit_dataframe)
unit_dataframe

qid                name      type  difficulty  max_accuracy_as_core  \
0     0                Abun      POSS           5              0.750000   
1     1                Ainu     ORDER           5              0.250000   
2     2         Ayutla Mixe     ORDER           4              0.500000   
3     3             Bangime     ORDER           3              1.000000   
4     4           Bangime 2     ORDER           1              1.000000   
5     5           Bangime 3     ORDER           4              0.600000   
6     6           Bangime 4     ORDER           2              0.400000   
7     7           Bangime 5     ORDER           3              1.000000   
8     8           Bangime 6  NOUN-ADJ           3              0.500000   
9     9           Bangime 7  NOUN-ADJ           4              1.000000   
10   10     Chimalapa Zoque     ORDER           5              0.000000   
11   11               Dogon      POSS           3              0.750000   
12   12             Dogon 2      POSS           4              0.500000   
13   13             Engenni     ORDER           3              1.000000   
14   14           Engenni 2     ORDER           2              1.000000   
15   15           Engenni 3     ORDER           3              1.000000   
16   16           Engenni 4     ORDER           2              1.000000   
17   17           Engenni 5     ORDER           3              1.000000   
18   18      Guugu Yimithir       SEM           5              0.600000   
19   19               Kalam       SEM           5              0.000000   
20   20          Komi-Ziran       SEM           5              0.333333   
21   21             Kutenai       SEM           5              1.000000   
22   22        Mapudungan 1  NOUN-ADJ           2              1.000000   
23   23        Mapudungan 2  NOUN-ADJ           2              1.000000   
24   24        Mapudungan 3  NOUN-ADJ           2              1.000000   
25   25        Mapudungan 4  NOUN-ADJ           2              1.000000   
26   26    Misantla Totonac  NOUN-ADJ           3              1.000000   
27   27    Mixtepec Zapotec  NOUN-ADJ           2              0.500000   
28   28  Mixtepec Zapotec 2  NOUN-ADJ           2              0.500000   
29   29  Mixtepec Zapotec 3  NOUN-ADJ           2              0.500000   
30   30  Mixtepec Zapotec 4  NOUN-ADJ           2              0.166667   
31   31            Ngadha 1  NOUN-ADJ           2              0.833333   
32   32            Ngadha 2  NOUN-ADJ           4              0.250000   
33   33              Niuean  NOUN-ADJ           3              1.000000   
34   34            Niuean 2  NOUN-ADJ           2              1.000000   
35   35            Niuean 3  NOUN-ADJ           2              1.000000   
36   36            Rapa Nui     ORDER           1              1.000000   
37   37          Rapa Nui 2     ORDER           4              1.000000   
38   38          Rapa Nui 3     ORDER           2              1.000000   
39   39          Rapa Nui 4     ORDER           3              1.000000   
40   40          Rapa Nui 5     ORDER           2              1.000000   
41   41          Rapa Nui 6  NOUN-ADJ           3              0.833333   
42   42          Rapa Nui 7  NOUN-ADJ           3              1.000000   
43   43                Seri  NOUN-ADJ           5              0.000000   
44   44              Seri 2     ORDER           5              0.750000   
45   45              Seri 3       SEM           5              0.600000   
46   46              Seri 4      POSS           5              0.750000   
47   47             Totonac      POSS           5              0.333333   

    mean_accuracy_as_core  min_accuracy_as_core  mean_accuracy_as_exemplar  \
0                0.643617              0.250000                   0.604610   
1                0.029255              0.000000                   0.585106   
2                0.255319              0.000000                   0.572695   
3               

In [ ]:
unit_dataframe["baseline_accuracy_v3"] = list(baseline_df.groupby("problem_name")["score"].mean())

In [ ]:
unit_dataframe

qid                name      type  difficulty  max_accuracy_as_core  \
0     0                Abun      POSS           5              0.750000   
1     1                Ainu     ORDER           5              0.250000   
2     2         Ayutla Mixe     ORDER           4              0.500000   
3     3             Bangime     ORDER           3              1.000000   
4     4           Bangime 2     ORDER           1              1.000000   
5     5           Bangime 3     ORDER           4              0.600000   
6     6           Bangime 4     ORDER           2              0.400000   
7     7           Bangime 5     ORDER           3              1.000000   
8     8           Bangime 6  NOUN-ADJ           3              0.500000   
9     9           Bangime 7  NOUN-ADJ           4              1.000000   
10   10     Chimalapa Zoque     ORDER           5              0.000000   
11   11               Dogon      POSS           3              0.750000   
12   12             Dogon 2      POSS           4              0.500000   
13   13             Engenni     ORDER           3              1.000000   
14   14           Engenni 2     ORDER           2              1.000000   
15   15           Engenni 3     ORDER           3              1.000000   
16   16           Engenni 4     ORDER           2              1.000000   
17   17           Engenni 5     ORDER           3              1.000000   
18   18      Guugu Yimithir       SEM           5              0.600000   
19   19               Kalam       SEM           5              0.000000   
20   20          Komi-Ziran       SEM           5              0.333333   
21   21             Kutenai       SEM           5              1.000000   
22   22        Mapudungan 1  NOUN-ADJ           2              1.000000   
23   23        Mapudungan 2  NOUN-ADJ           2              1.000000   
24   24        Mapudungan 3  NOUN-ADJ           2              1.000000   
25   25        Mapudungan 4  NOUN-ADJ           2              1.000000   
26   26    Misantla Totonac  NOUN-ADJ           3              1.000000   
27   27    Mixtepec Zapotec  NOUN-ADJ           2              0.500000   
28   28  Mixtepec Zapotec 2  NOUN-ADJ           2              0.500000   
29   29  Mixtepec Zapotec 3  NOUN-ADJ           2              0.500000   
30   30  Mixtepec Zapotec 4  NOUN-ADJ           2              0.166667   
31   31            Ngadha 1  NOUN-ADJ           2              0.833333   
32   32            Ngadha 2  NOUN-ADJ           4              0.250000   
33   33              Niuean  NOUN-ADJ           3              1.000000   
34   34            Niuean 2  NOUN-ADJ           2              1.000000   
35   35            Niuean 3  NOUN-ADJ           2              1.000000   
36   36            Rapa Nui     ORDER           1              1.000000   
37   37          Rapa Nui 2     ORDER           4              1.000000   
38   38          Rapa Nui 3     ORDER           2              1.000000   
39   39          Rapa Nui 4     ORDER           3              1.000000   
40   40          Rapa Nui 5     ORDER           2              1.000000   
41   41          Rapa Nui 6  NOUN-ADJ           3              0.833333   
42   42          Rapa Nui 7  NOUN-ADJ           3              1.000000   
43   43                Seri  NOUN-ADJ           5              0.000000   
44   44              Seri 2     ORDER           5              0.750000   
45   45              Seri 3       SEM           5              0.600000   
46   46              Seri 4      POSS           5              0.750000   
47   47             Totonac      POSS           5              0.333333   

    mean_accuracy_as_core  min_accuracy_as_core  mean_accuracy_as_exemplar  \
0                0.643617              0.250000                   0.604610   
1                0.029255              0.000000                   0.585106   
2                0.255319              0.000000                   0.572695   
3               

In [ ]:
unit_dataframe.to_csv("unit_dataframe.csv", index=False)